In [2]:
#Importamos las librerias necesarias para el análisis de datos 
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import os
import sys
#Importamos plotly para la visualización de los datos
import plotly.express as px
import plotly.graph_objects as go

In [3]:
df = pd.read_csv(r'C:\Users\spide\Desktop\Bootcamp\mi_entorno\Modulo_3\proyecto_final_modulo_3\vehiculos-de-segunda-mano-sample.csv',encoding = 'UTF-8')

In [4]:
df.shape

(100000, 28)

In [5]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100000 entries, 0 to 99999
Data columns (total 28 columns):
 #   Column                  Non-Null Count   Dtype  
---  ------                  --------------   -----  
 0   vehicle_type            100000 non-null  object 
 1   make                    100000 non-null  object 
 2   model                   100000 non-null  object 
 3   version                 99842 non-null   object 
 4   fuel                    96810 non-null   object 
 5   year                    100000 non-null  int64  
 6   kms                     99189 non-null   float64
 7   power                   99709 non-null   float64
 8   doors                   0 non-null       float64
 9   shift                   98982 non-null   object 
 10  color                   0 non-null       float64
 11  photos                  100000 non-null  int64  
 12  description             55810 non-null   object 
 13  price                   100000 non-null  int64  
 14  currency             

## Selección de variables que usaremos para el estudio

In [6]:
df.columns

Index(['vehicle_type', 'make', 'model', 'version', 'fuel', 'year', 'kms',
       'power', 'doors', 'shift', 'color', 'photos', 'description', 'price',
       'currency', 'location', 'publish_date', 'update_date', 'dealer_name',
       'dealer_description', 'dealer_address', 'dealer_zip_code',
       'dealer_city', 'dealer_country_code', 'dealer_is_professional',
       'dealer_website', 'dealer_registered_at', 'date'],
      dtype='object')

* Eliminaremos *vehicle_type* debido a que solo tiene el valor único car.
* Eliminaremos *doors* debido a que tiene un 100% de valores nulos, al igual que *colors*.
* Eliminaremos *currency* debido a que solo es el tipo de moneda.
* *update_date* la borraremos debido a que no nos da información para el análisis.
* Eliminaremos *dealer_name*, *dealer_description*, *dealer_city*, *dealer_zip_code*, *dealer_city*, *dealer_country_code*, *dealer_is_professional*, *dealer_website*, *dealer_registered_at*, *date* porque no nos aportan información en nuestro análisis.

In [7]:
df = df.drop(['vehicle_type','doors','color','photos', 'description','currency','update_date','dealer_name','dealer_description', 'dealer_is_professional','dealer_website','dealer_registered_at', 'date'], axis=1)

## Valores duplicados


In [8]:
df.duplicated().sum() #filas duplicadas

57295

In [9]:
df = df.drop_duplicates()

## Valores nulos

In [10]:
df.isnull().sum()

make                      0
model                     0
version                  73
fuel                   1280
year                      0
kms                     250
power                    83
shift                   697
price                     0
location                  0
publish_date              0
dealer_address           27
dealer_zip_code          27
dealer_city              27
dealer_country_code       0
dtype: int64

In [11]:
((df.isnull().sum())/df.shape[0])*100

make                   0.000000
model                  0.000000
version                0.170940
fuel                   2.997307
year                   0.000000
kms                    0.585412
power                  0.194357
shift                  1.632127
price                  0.000000
location               0.000000
publish_date           0.000000
dealer_address         0.063224
dealer_zip_code        0.063224
dealer_city            0.063224
dealer_country_code    0.000000
dtype: float64

### Valores nulos de tipo de combustible

In [12]:
# Ajustar las opciones de visualización de pandas
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', None)

# Mostrar el resultado completo
df[df['fuel'].isnull()][['make','model']].value_counts()

make           model             
Toyota         C-HR                  253
               Corolla                62
Ford           Puma                   53
Fiat           500                    44
Mazda          2                      39
KIA            Ceed                   39
Lexus          NX                     39
Toyota         Auris                  37
               Yaris                  36
KIA            Sportage               35
Hyundai        IONIQ                  29
Renault        Arkana                 29
Lexus          ES                     27
SEAT           Leon                   25
Lexus          UX                     25
KIA            Niro                   22
Citroen        C3                     22
Lexus          RX                     21
               IS                     19
BMW            Serie 4                19
Hyundai        Tucson                 17
CUPRA          Leon                   17
Lexus          RC                     16
Fiat           Panda   

In [13]:
df = df.dropna(subset=['kms', 'version'])

In [14]:
((df.isnull().sum())/df.shape[0])*100
    

make                   0.000000
model                  0.000000
version                0.000000
fuel                   2.968241
year                   0.000000
kms                    0.000000
power                  0.179321
shift                  1.625690
price                  0.000000
location               0.000000
publish_date           0.000000
dealer_address         0.063706
dealer_zip_code        0.063706
dealer_city            0.063706
dealer_country_code    0.000000
dtype: float64

In [15]:
# Lista de variables a rellenar
variables = ['fuel', 'power', 'shift']

# Función para calcular la moda o mediana por modelo
def calculate_stat_by_model(df, var):
    if var == 'power':
        return df.groupby('model')[var].transform(lambda x: x.median() if not pd.isna(x.median()) else None)
    else:
        return df.groupby('model')[var].transform(lambda x: x.mode()[0] if not x.mode().empty else None)

# Función para rellenar los valores nulos
def fill_missing_values(df, var):
    stat_by_model = calculate_stat_by_model(df, var)
    df[var] = df[var].fillna(stat_by_model)
    return df

# Aplicar la función para cada variable
for var in variables:
    df = fill_missing_values(df, var)


C:\Users\spide\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\numpy\lib\nanfunctions.py:1215: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)


In [16]:
df.isnull().sum()    

make                    0
model                   0
version                 0
fuel                    3
year                    0
kms                     0
power                   1
shift                   1
price                   0
location                0
publish_date            0
dealer_address         27
dealer_zip_code        27
dealer_city            27
dealer_country_code     0
dtype: int64

In [17]:
#Estos los arreglaremos poniendole gasolina porque lo hemos busucado en internet
df['fuel'] = df['fuel'].fillna('Gasolina')

In [18]:
df[df['power'].isnull()][['make','model']].value_counts() #Vemos los valores nulos de la variable power que nos quedan

make     model  
Citroen  ë-Jumpy    1
Name: count, dtype: int64

In [19]:
#Buscando en internet tiene 100 kW
df['power'] = df['power'].fillna(100.0)

In [20]:
df[df['shift'].isnull()][['make','model','version']].value_counts() #Vemos los valores nulos de la variable shift que nos quedan

make   model   version             
Lotus  Esprit  Coche de competición    1
Name: count, dtype: int64

In [21]:
#Buscando en internet el vehículo es manual
df['shift']=df['shift'].fillna('manual')

In [22]:
df.isnull().sum()   

make                    0
model                   0
version                 0
fuel                    0
year                    0
kms                     0
power                   0
shift                   0
price                   0
location                0
publish_date            0
dealer_address         27
dealer_zip_code        27
dealer_city            27
dealer_country_code     0
dtype: int64

In [23]:
df[df['dealer_zip_code'].isnull()]['location'].value_counts()

location
Elx/Elche                                     21
Parque Empresarial San Fernando de Henares     5
Collado Villalba                               1
Name: count, dtype: int64

In [24]:
#Pasamos a texto el valor de dealer_zip_code por aquellos que empiezen por 0
df['dealer_zip_code'] = df['dealer_zip_code'].astype(str)

In [25]:
df.loc[df['location'] == 'Parque Empresarial San Fernando de Henares', 'dealer_zip_code'] = df.loc[df['location'] == 'Parque Empresarial San Fernando de Henares', 'dealer_zip_code'].fillna('28830')
df.loc[df['location'] == 'Collado Villalba', 'dealer_zip_code'] = df.loc[df['location'] == 'Collado Villalba', 'dealer_zip_code'].fillna('28400')
df.loc[df['location'] == 'Elx/Elche', 'dealer_zip_code'] = df.loc[df['location'] == 'Elx/Elche', 'dealer_zip_code'].fillna('03203')

In [26]:
df.isnull().sum()   

make                    0
model                   0
version                 0
fuel                    0
year                    0
kms                     0
power                   0
shift                   0
price                   0
location                0
publish_date            0
dealer_address         27
dealer_zip_code         0
dealer_city            27
dealer_country_code     0
dtype: int64

In [27]:
df = df.dropna(subset=['dealer_address'])

In [28]:
df.isnull().sum()

make                   0
model                  0
version                0
fuel                   0
year                   0
kms                    0
power                  0
shift                  0
price                  0
location               0
publish_date           0
dealer_address         0
dealer_zip_code        0
dealer_city            0
dealer_country_code    0
dtype: int64

In [29]:
#Guardar df en csv 
#df.to_csv('car_price.csv', index=False)

## Latitud, Longitud y Provincia

In [39]:

import pandas as pd
from geopy.geocoders import Nominatim
from geopy.exc import GeocoderTimedOut, GeocoderServiceError
import time

def clean_address(address):
    """
    Limpia y formatea la dirección
    """
    if pd.isna(address):
        return ""
    # Convertir a string si no lo es
    address = str(address)
    # Eliminar caracteres especiales y espacios extras
    address = address.replace("NaN", "").strip()
    return address

def get_coordinates(address, city, country_code):
    """
    Get latitude and longitude from address using Nominatim geocoder
    """
    # Limpiar los componentes de la dirección
    address = clean_address(address)
    city = clean_address(city)
    country_code = clean_address(country_code)
    
    # Si no hay suficiente información, retornar None
    if not (address and city and country_code):
        print(f"Información incompleta: {address}, {city}, {country_code}")
        return None, None
    
    # Crear la dirección completa
    full_address = f"{address}, {city}, {country_code}"
    print(f"Buscando dirección: {full_address}")  # Para depuración
    
    # Initialize the geocoder
    geolocator = Nominatim(user_agent="my_vehicles_app")
    
    try:
        time.sleep(1)  # Respetar límites de la API
        
        # Intentar primero con la dirección completa
        location = geolocator.geocode(full_address)
        
        # Si falla, intentar solo con ciudad y país
        if not location:
            print("Intentando con ciudad y país...")
            location = geolocator.geocode(f"{city}, {country_code}")
        
        if location:
            print(f"Encontrado: {location.latitude}, {location.longitude}")
            return location.latitude, location.longitude
        else:
            print("No se encontró la ubicación")
            return None, None
            
    except (GeocoderTimedOut, GeocoderServiceError) as e:
        print(f"Error de geocodificación: {str(e)}")
        return None, None

def get_province_from_coordinates(lat, long):
    """
    Obtiene la provincia utilizando las coordenadas de latitud y longitud
    """
    if lat is None or long is None:
        return 'Unknown'
    
    geolocator = Nominatim(user_agent="my_vehicles_app")
    try:
        time.sleep(1)  # Respetar límites de la API
        location = geolocator.reverse((lat, long), timeout=10).raw['address']
        print(f"Provincia encontrada: {location.get('state', 'Unknown')}")  # 'state' puede variar dependiendo del país
        return location.get('state', 'Unknown'),  # 'state' puede variar dependiendo del país
    except (GeocoderTimedOut, GeocoderServiceError, KeyError) as e:
        print(f"Error al obtener la provincia: {str(e)}")
        return 'Unknown'

def add_coordinates_and_state_to_df(df):
    """
    Add latitude, longitude, and state columns to the DataFrame
    """
    # Initialize new columns
    df['lat'] = None
    df['long'] = None
    df['state'] = None
    
    # Iterate through rows
    for idx, row in df.iterrows():
        print(f"\nProcesando fila {idx + 1}/{len(df)}")
        
        # Imprimir los valores para depuración
        print(f"Dirección: {row.get('dealer_address', 'No disponible')}")
        print(f"Ciudad: {row.get('dealer_city', 'No disponible')}")
        print(f"País: {row.get('dealer_country_code', 'No disponible')}")
        
        # Obtener latitud y longitud
        lat, long = get_coordinates(
            row.get('dealer_address', ''),
            row.get('dealer_city', ''),
            row.get('dealer_country_code', '')
        )
        
        # Obtener la provincia si se encontraron coordenadas
        state = get_province_from_coordinates(lat, long)
        
        # Actualizar el DataFrame
        df.at[idx, 'lat'] = lat
        df.at[idx, 'long'] = long
        df.at[idx, 'state'] = state
    
    return df

IndentationError: unexpected indent (3164020817.py, line 9)

Usamos la función de arriba para encontrar la comunidad autónoma, latitud y longitud. Como se basa en la variable *"location"*  depende de que formato tenga, el geolocalizador no encuentra bien los valores deseados y devuelve *Unknown* cuando no encuentra la comunidad autónoma y valres nulos para la latitud y la longitud. 

In [38]:
#df =df.add_coordinates_and_state_to_df(df)

Después de correr la función anterior nos quedaron 4000 valores nulos. El resultado de correr el codigo lo sacamos de dffinal:


In [47]:
df_final = pd.read_csv("dffinal.csv")

In [49]:
df_final.isnull().sum()

make                      0
model                     0
version                   0
fuel                      0
year                      0
kms                       0
power                     0
shift                     0
price                     0
location                  0
publish_date              0
dealer_address            0
dealer_zip_code           0
dealer_city               0
dealer_country_code       0
lat                    4350
long                   4350
state                     0
dtype: int64

In [51]:
df_final[df_final['lat'].isnull()]['location'].value_counts()

location
Mercado Parque Corredor del Henares                         629
Colonia Pablo Iglesias                                      609
Ciudad Real                                                 553
Santiago de Compostela                                      386
Hidraulica Santillana                                       359
Bilbao                                                      227
Málaga                                                      226
Urbanizacion La Granjilla                                   176
Valdepeñas                                                  134
Barcelona                                                   134
Vigo                                                        123
Almería                                                     111
Torremolinos                                                 81
Armentia                                                     79
Urbanitzacio El Medol                                        49
Castello/Castellon de La Plana 

Nos dividimos la tarea entre los miembros del grupo para bucar los parámetros faltantes a mano y los juntamos todos en un mismo diccionario.

In [70]:
missing_coords_3 = {
    'Fuengirola': {'latitud': 36.5397, 'longitud': -4.6243, 'state': 'Andalucía'},
    'Puebla de la Calzada': {'latitud': 38.9227, 'longitud': -6.1362, 'state': 'Extremadura'},
    'Cañada Hermosa': {'latitud': 38.5425, 'longitud': -1.5119, 'state': 'Región de Murcia'},
    'Fuenlabrada': {'latitud': 40.2897, 'longitud': -3.7985, 'state': 'Comunidad de Madrid'},
    'Donostia-San Sebastián': {'latitud': 43.3183, 'longitud': -1.9812, 'state': 'País Vasco'},
    'Camarma de Esteruelas': {'latitud': 40.5145, 'longitud': -3.3632, 'state': 'Comunidad de Madrid'},
    'Saladar': {'latitud': 38.1182, 'longitud': -0.2899, 'state': 'Comunidad Valenciana'},
    'Santander': {'latitud': 43.4623, 'longitud': -3.8099, 'state': 'Cantabria'},
    'Barbastro': {'latitud': 42.0509, 'longitud': 0.1325, 'state': 'Aragón'},
    'Oviedo': {'latitud': 43.3611, 'longitud': -5.8494, 'state': 'Asturias'},
    'Granollers': {'latitud': 41.6085, 'longitud': 2.2880, 'state': 'Cataluña'},
    'Las Vegas': {'latitud': 40.2487, 'longitud': -3.7243, 'state': 'Comunidad de Madrid'},
    'Huelva': {'latitud': 37.2614, 'longitud': -6.9447, 'state': 'Andalucía'},
    'Las Rozas de Madrid': {'latitud': 40.4722, 'longitud': -3.8707, 'state': 'Comunidad de Madrid'},
    'Girona': {'latitud': 41.9794, 'longitud': 2.8217, 'state': 'Cataluña'},
    'Palau-Solità i Plegamans': {'latitud': 41.5993, 'longitud': 2.2297, 'state': 'Cataluña'},
    'Villaviciosa de Odón': {'latitud': 40.3530, 'longitud': -3.8610, 'state': 'Comunidad de Madrid'},
    'Palma de Mallorca': {'latitud': 39.5696, 'longitud': 2.6502, 'state': 'Islas Baleares'},
    'Tarragona': {'latitud': 41.1189, 'longitud': 1.2445, 'state': 'Cataluña'},
    'Ullastrell': {'latitud': 41.4932, 'longitud': 1.9159, 'state': 'Cataluña'},
    'Òrrius': {'latitud': 41.6583, 'longitud': 2.3485, 'state': 'Cataluña'},
    'Sant Boi de Llobregat': {'latitud': 41.3305, 'longitud': 2.0332, 'state': 'Cataluña'},
    'Granada': {'latitud': 37.1882, 'longitud': -3.6066, 'state': 'Andalucía'},
    'Terrassa': {'latitud': 41.5633, 'longitud': 2.0082, 'state': 'Cataluña'},
    'La Zubia': {'latitud': 37.1350, 'longitud': -3.6505, 'state': 'Andalucía'},
    'Leioa': {'latitud': 43.3144, 'longitud': -2.9791, 'state': 'País Vasco'},
    'Olèrdola': {'latitud': 41.2849, 'longitud': 1.7794, 'state': 'Cataluña'},
    'Cieza': {'latitud': 38.2444, 'longitud': -1.4417, 'state': 'Región de Murcia'},
    'Urbi': {'latitud': 39.8320, 'longitud': -4.7962, 'state': 'Castilla-La Mancha'},
    'Caravaca de la Cruz': {'latitud': 38.1254, 'longitud': -1.8700, 'state': 'Región de Murcia'},
    'Polígono Industrial Parque Industrial de Elche': {'latitud': 38.2693, 'longitud': -0.7039, 'state': 'Comunidad Valenciana'},
    'El Puerto de Santa María': {'latitud': 36.5950, 'longitud': -6.2336, 'state': 'Andalucía'},
    'Residencial Can Carner': {'latitud': 41.6110, 'longitud': 1.9024, 'state': 'Cataluña'},
    'Estepona': {'latitud': 36.4250, 'longitud': -5.1446, 'state': 'Andalucía'},
    'Los Palacios y Villafranca': {'latitud': 37.2864, 'longitud': -5.8597, 'state': 'Andalucía'},
    'Varea': {'latitud': 42.4576, 'longitud': -2.4925, 'state': 'La Rioja'},
    'Santa Cruz Santa Cruz': {'latitud': 38.0860, 'longitud': -1.2011, 'state': 'Región de Murcia'},
    'Cogullada': {'latitud': 42.2150, 'longitud': -2.4369, 'state': 'La Rioja'},
    'Ugarte': {'latitud': 42.8392, 'longitud': -2.9681, 'state': 'País Vasco'},
    'Sant Vicenç de Montalt': {'latitud': 41.5850, 'longitud': 2.5333, 'state': 'Cataluña'},
    'Los Yébenes': {'latitud': 39.7697, 'longitud': -3.4643, 'state': 'Castilla-La Mancha'},
    'Albatera': {'latitud': 38.2328, 'longitud': -0.8174, 'state': 'Comunidad Valenciana'},
    'Hidraulica Santillana': {'latitud': 40.6667, 'longitud': -3.7667, 'state': 'Comunidad de Madrid'},
    'Polígono Industrial San Fernando': {'latitud': 36.4630, 'longitud': 6.1880, 'state': 'Andalucía'},
    'Polígono Da Louzaneta': {'latitud': 43.0000, 'longitud': -7.5500, 'state': 'Galicia'},
    'San José de La Rinconada': {'latitud': 37.4000, 'longitud': 5.8430, 'state': 'Andalucía'},
    'Castelló/Castellón de La Plana': {'latitud': 39.9860, 'longitud': 0.0350, 'state': 'Comunidad Valenciana'},
    'La Nucia-Hill Nucia Hills': {'latitud': 38.6500, 'longitud': -0.1500, 'state': 'Comunidad Valenciana'},
    'Urbanización Beltraneja': {'latitud': 40.3667, 'longitud': -3.7667, 'state': 'Comunidad de Madrid'},
    'Urbanización Calipo': {'latitud': 40.5510, 'longitud': 3.6490, 'state': 'Comunidad de Madrid'},
    'Polígono Industrial Madanela': {'latitud': 40.4190, 'longitud': 3.5790, 'state': 'Comunidad de Madrid'},
    'Urbanización Las Bizarricas': {'latitud': 40.4710, 'longitud': 4.0640, 'state': 'Castilla-La Mancha'},
    'Plataforma Logística Plaza': {'latitud': 41.6560, 'longitud': 0.9470, 'state': 'Aragón'},
    'Palau-Solita i Plegamans': {'latitud': 41.5885, 'longitud': 2.1730, 'state': 'Cataluña'},
    'Poligono Industrial Parque Industrial de Elche': {'latitud': 38.2760, 'longitud': 0.7100,'state': 'Comunidad Valenciana'}
}


In [71]:
missing_coords_1 = {
    'Málaga': {'latitud': 36.7213, 'longitud': -4.4217, 'state': 'Andalucía'},
    'Almería': {'latitud': 36.8381, 'longitud': -2.4587, 'state': 'Andalucía'},
    'Vigo': {'latitud': 42.2406, 'longitud': -8.7207, 'state': 'Galicia'},
    'Colonia Pablo Iglesias': {'latitud': 40.3703, 'longitud': -3.7361, 'state': 'state de Madrid'},
    'Bilbao': {'latitud': 43.2630, 'longitud': -2.9340, 'state': 'País Vasco'},
    'Santiago de Compostela': {'latitud': 42.8805, 'longitud': -8.5460, 'state': 'Galicia'},
    'Mercado Parque Corredor del Henares': {'latitud': 40.4667, 'longitud': -3.3640, 'state': 'state de Madrid'},
    'Ciudad Real': {'latitud': 38.9780, 'longitud': -3.9300, 'state': 'Castilla-La Mancha'},
    'Hidráulica Santillana': {'latitud': 43.3701, 'longitud': -4.0844, 'state': 'Cantabria'},
    'Valdepeñas': {'latitud': 38.7667, 'longitud': -3.0000, 'state': 'Castilla-La Mancha'},
    'Urbanitzacio El Medol': {'latitud': 41.1307, 'longitud': 0.8374, 'state': 'Cataluña'},
    'Torredonjimeno': {'latitud': 37.8181, 'longitud': -3.6982, 'state': 'Andalucía'},
    'Urbanizacion La Granjilla': {'latitud': 40.3570, 'longitud': -3.7850, 'state': 'state de Madrid'},
    'Collado Villalba': {'latitud': 40.6365, 'longitud': -3.9862, 'state': 'state de Madrid'},
    'Torrejón de Ardoz': {'latitud': 40.4551, 'longitud': -3.4743, 'state': 'state de Madrid'},
    'Barcelona': {'latitud': 41.3784, 'longitud': 2.1915, 'state': 'Cataluña'},
    'Gijón': {'latitud': 43.5366, 'longitud': -5.6613, 'state': 'Asturias'},
    'Polígono Industrial San Fernando': {'latitud': 37.3960, 'longitud': -5.9736, 'state': 'Andalucía'},
    'Coiros de Arriba': {'latitud': 43.2474, 'longitud': -8.1393, 'state': 'Galicia'},
    'Viladecans': {'latitud': 41.3254, 'longitud': 2.0221, 'state': 'Cataluña'},
    'Villanueva del Arzobispo': {'latitud': 38.2299, 'longitud': -3.2671, 'state': 'Andalucía'},
    'Polígono Da Louzaneta': {'latitud': 42.3565, 'longitud': -8.4120, 'state': 'Galicia'},
    'Balmaseda': {'latitud': 43.1460, 'longitud': -3.2530, 'state': 'País Vasco'},
    'Badalona': {'latitud': 41.4507, 'longitud': 2.2462, 'state': 'Cataluña'},
    'San José de La Rinconada': {'latitud': 37.4346, 'longitud': -5.8710, 'state': 'Andalucía'},
    'Murcia': {'latitud': 37.9836, 'longitud': -1.1280, 'state': 'Región de Murcia'},
    'Valencia': {'latitud': 39.4699, 'longitud': -0.3763, 'state': 'state Valenciana'},
    'Castellón de la Plana': {'latitud': 39.9864, 'longitud': -0.0561, 'state': 'state Valenciana'},
    'Mérida': {'latitud': 38.9198, 'longitud': -6.3430, 'state': 'Extremadura'},
    'Madrid': {'latitud': 40.4168, 'longitud': -3.7038, 'state': 'state de Madrid'},
    'Torrellano': {'latitud': 38.2222, 'longitud': -0.5789, 'state': 'state Valenciana'},
    'Mercabilbao': {'latitud': 43.2913, 'longitud': -2.9314, 'state': 'País Vasco'},
    'Nava': {'latitud': 43.3503, 'longitud': -5.5043, 'state': 'Asturias'},
    'Partida Altabix': {'latitud': 38.2604, 'longitud': -0.6904, 'state': 'state Valenciana'},
    'Sevilla': {'latitud': 37.3886, 'longitud': -5.9823, 'state': 'Andalucía'},
    'Ávila': {'latitud': 40.6539, 'longitud': -4.6793, 'state': 'Castilla y León'},
    'Armentia': {'latitud': 42.8579, 'longitud': -2.7183, 'state': 'País Vasco'},
    'Torremolinos': {'latitud': 36.6202, 'longitud': -4.5014, 'state': 'Andalucía'},
    'Ciudad Deportiva del Jarama': {'latitud': 40.5391, 'longitud': -3.4782, 'state': 'state de Madrid'}
}


In [72]:
missing_coords_2 = {
    'El Cuervo': {'latitud': 37.0384, 'longitud': -6.0889, 'state': 'Andalucía'},
    'Zaragoza': {'latitud': 41.6488, 'longitud': -0.8891, 'state': 'Aragón'},
    'La Nucia-Hill Nucia Hills': {'latitud': 38.6536, 'longitud': -0.1669, 'state': 'state Valenciana'},
    'Urbanización Beltraneja': {'latitud': 40.3894, 'longitud': -3.7465, 'state': 'state de Madrid'},
    'Córdoba': {'latitud': 37.8882, 'longitud': -4.7794, 'state': 'Andalucía'},
    "El Moli d'en Rovira": {'latitud': 41.2886, 'longitud': 2.1628, 'state': 'Cataluña'},
    'Santa Coloma de Gramenet': {'latitud': 41.2115, 'longitud': 2.2269, 'state': 'Cataluña'},
    'Gamarra Mayor': {'latitud': 42.4075, 'longitud': -2.4869, 'state': 'País Vasco'},
    'Villena': {'latitud': 38.5507, 'longitud': -0.6200, 'state': 'state Valenciana'},
    'Linares': {'latitud': 38.0996, 'longitud': -3.6680, 'state': 'Andalucía'},
    'Mula': {'latitud': 38.0864, 'longitud': -1.4206, 'state': 'Región de Murcia'},
    'Urbanización Calipo': {'latitud': 39.4978, 'longitud': -0.4014, 'state': 'state Valenciana'},
    'Gamarra Menor': {'latitud': 42.3766, 'longitud': -2.4978, 'state': 'País Vasco'},
    'Algeciras': {'latitud': 36.1408, 'longitud': -5.4592, 'state': 'Andalucía'},
    'Santa Maria del Aguila': {'latitud': 37.0533, 'longitud': -2.5644, 'state': 'Andalucía'},
    'Castellón': {'latitud': 39.9864, 'longitud': -0.0561, 'state': 'state Valenciana'},
    'Carretera Castro de Elviña': {'latitud': 43.3696, 'longitud': -8.3944, 'state': 'Galicia'},
    'Polígono Industrial Madanela': {'latitud': 43.3710, 'longitud': -8.3881, 'state': 'Galicia'},
    'Vitoria-Gasteiz': {'latitud': 42.8500, 'longitud': -2.6666, 'state': 'País Vasco'},
    'Emisora Radio Elect Campillo': {'latitud': 38.4672, 'longitud': -1.8650, 'state': 'Región de Murcia'},
    'Santa Perpètua de Mogoda': {'latitud': 41.4981, 'longitud': 2.2077, 'state': 'Cataluña'},
    'Cádiz': {'latitud': 36.5311, 'longitud': -6.2919, 'state': 'Andalucía'},
    'Alicante/Alacant': {'latitud': 38.3452, 'longitud': -0.4810, 'state': 'state Valenciana'},
    'Santafe': {'latitud': 37.5269, 'longitud': -3.6892, 'state': 'Andalucía'},
    'Toledo': {'latitud': 39.8628, 'longitud': -4.0273, 'state': 'Castilla-La Mancha'},
    'Sant Andreu de la Barca': {'latitud': 41.5142, 'longitud': 1.9440, 'state': 'Cataluña'},
    'Albacete': {'latitud': 38.9949, 'longitud': -1.8585, 'state': 'Castilla-La Mancha'},
    'Mijas': {'latitud': 36.5958, 'longitud': -4.6292, 'state': 'Andalucía'},
    'Badajoz': {'latitud': 38.8795, 'longitud': -6.9703, 'state': 'Extremadura'},
    'Alfafar': {'latitud': 39.4510, 'longitud': -0.3833, 'state': 'state Valenciana'},
    'Urbanitzacio Can Valls-To': {'latitud': 41.4815, 'longitud': 2.1243, 'state': 'Cataluña'},
    'Urbanización Las Bizarricas': {'latitud': 38.5333, 'longitud': -0.4528, 'state': 'state Valenciana'},
    'Cúllar Vega': {'latitud': 37.1471, 'longitud': -3.5902, 'state': 'Andalucía'},
    'Mollet del Vallès': {'latitud': 41.5440, 'longitud': 2.1882, 'state': 'Cataluña'},
    'El Aeroport del Prat': {'latitud': 41.2973, 'longitud': 2.0787, 'state': 'Cataluña'},
    'Sax': {'latitud': 38.5325, 'longitud': -0.7819, 'state': 'state Valenciana'},
    'Santa Pola': {'latitud': 38.1884, 'longitud': -0.5452, 'state': 'state Valenciana'},
    'Parla': {'latitud': 40.2330, 'longitud': -3.7680, 'state': 'state de Madrid'},
    'Burgos': {'latitud': 42.3417, 'longitud': -3.6969, 'state': 'Castilla y León'},
    'Alameda del Obispo': {'latitud': 37.8493, 'longitud': -4.7710, 'state': 'Andalucía'},
    'Armunia': {'latitud': 42.4729, 'longitud': -5.6643, 'state': 'Castilla y León'},
    'Carretera del Km. 17,500 Al 22,600 Madrid-Colmenar Viejo': {'latitud': 40.5566, 'longitud': -3.7054, 'state': 'state de Madrid'},
    'Pamplona/Iruña': {'latitud': 42.8197, 'longitud': -1.6463, 'state': 'Navarra'},
    'Alcobendas': {'latitud': 40.5354, 'longitud': -3.6371, 'state': 'state de Madrid'},
    'Marbella': {'latitud': 36.5130, 'longitud': -4.8823, 'state': 'Andalucía'},
    'Orihuela': {'latitud': 38.0887, 'longitud': -0.9482, 'state': 'state Valenciana'},
    "L' Alcudia de Crespins": {'latitud': 39.1232, 'longitud': -0.4607, 'state': 'state Valenciana'},
    'Colonia Rocafiguera': {'latitud': 41.3799, 'longitud': 2.0025, 'state': 'Cataluña'},
    'Plataforma Logística Plaza': {'latitud': 41.6539, 'longitud': -0.8763, 'state': 'Aragón'}
}


In [73]:
# Unir los tres diccionarios en uno solo
missing_coords_combined = {**missing_coords_1, **missing_coords_2, **missing_coords_3}

# Verificar la unión
print(len(missing_coords_combined))  # Debería ser la suma de las longitudes de los tres diccionarios

134


In [74]:
df_final.columns

Index(['make', 'model', 'version', 'fuel', 'year', 'kms', 'power', 'shift',
       'price', 'location', 'publish_date', 'dealer_address',
       'dealer_zip_code', 'dealer_city', 'dealer_country_code', 'lat', 'long',
       'state'],
      dtype='object')

In [75]:

for location, coords in missing_coords_combined.items():
    df_final.loc[df_final['location'] == location, ['lat', 'long', 'state']] = coords['latitud'], coords['longitud'], coords['state']

# Mostrar las filas actualizadas para verificar
print(df_final[df_final['location'].isin(missing_coords_combined.keys())][['location', 'lat', 'long', 'state']])

                                                       location      lat  \
2                                                        Madrid  40.4168   
4                                             Mollet del Vallès  41.5440   
5                                                        Málaga  36.7213   
6                                                        Málaga  36.7213   
7                                                      Badalona  41.4507   
8                                         Sant Boi de Llobregat  41.3305   
9                                                       Almería  36.8381   
10                                                       Málaga  36.7213   
11                                                         Vigo  42.2406   
13                                                     Valencia  39.4699   
15                                                    Barcelona  41.3784   
16                                        Camarma de Esteruelas  40.5145   
17          

In [76]:
df_final.isnull().sum() 

make                   0
model                  0
version                0
fuel                   0
year                   0
kms                    0
power                  0
shift                  0
price                  0
location               0
publish_date           0
dealer_address         0
dealer_zip_code        0
dealer_city            0
dealer_country_code    0
lat                    0
long                   0
state                  0
dtype: int64

In [79]:
df_final[df_final['state']=="Unknown"]['location'].value_counts()

location
Atarrabia                           357
Castello/Castellon de La Plana       34
Poligono Industrial Madanela         13
Monteagudo                           13
La / Nucia-Hill Nucia Hills           7
Aizoain                               6
Orkoien                               6
Poligono Industrial San Fernando      5
Urbanizacion Beltraneja               4
Tajonar/Taxoare                       3
San Jose de La Rinconada              3
El Guincho                            3
Artajona                              2
Urbanizacion Calipo                   2
Poligono Da Louzaneta                 2
Ibiricu de Egües                      2
La Hornera                            2
Tudela                                2
Las Chafiras                          1
Plataforma Logistica Plaza            1
Las Parcelas                          1
Tamaraceite                           1
Urbanizacion Las Bizarricas           1
Aeropuerto de Noain                   1
Palau-Solita I Plegamans       

Arrreglamos los ultimos unknown que por inconsistencias tipográficas no hemos podido detectar en el anterior diccionario.

In [92]:
df_final[df_final['location']=='Aeropuerto de Noain']

make model                          version    fuel  year      kms  \
14110  Volvo  XC40  2.0 D4 190 Momentum AWD 5p Aut.  Diésel  2018  99000.0   

       power      shift  price             location publish_date  \
14110  190.0  automatic  31900  Aeropuerto de Noain   2023-01-28   

                                                                                                                                    dealer_address  \
14110  Travesía de Noáin, Noáin, Noáin (Valle de Elorz)/Noain (Elortzibar), Metropolialdea / Área Metropolitana, Navarra - Nafarroa, 31110, España   

       dealer_zip_code          dealer_city dealer_country_code        lat  \
14110          31110.0  Aeropuerto de Noain                  ES  42.771144   

           long    state  
14110 -1.645621  Unknown

In [93]:
lugares = {
    "Atarrabia": 'Comunidad Foral de Navarra',
    "Castello/Castellon de La Plana": 'Comunidad Valenciana',
    "Poligono Industrial Madanela": 'Comunidad de Madrid',
    "Monteagudo": 'Región de Murcia',
    "La / Nucia-Hill Nucia Hills": 'Comunidad Valenciana',
    "Aizoain": 'Comunidad Foral de Navarra',
    "Orkoien": 'Comunidad Foral de Navarra',
    "Poligono Industrial San Fernando": 'Comunidad de Madrid',
    "Urbanizacion Beltraneja": 'Castilla-La Mancha',
    "Tajonar/Taxoare": 'Comunidad Foral de Navarra',
    "San Jose de La Rinconada": 'Andalucía',
    "El Guincho": 'Canarias',
    "Artajona": 'Comunidad Foral de Navarra',
    "Urbanizacion Calipo": 'Comunidad de Madrid',
    "Poligono Da Louzaneta": 'Galicia',
    "Ibiricu de Egües": 'Comunidad Foral de Navarra',
    "La Hornera": 'Región de Murcia',
    "Tudela": 'Comunidad Foral de Navarra',
    "Las Chafiras": 'Canarias',
    "Plataforma Logistica Plaza": 'Aragón',
    "Las Parcelas": 'Región de Murcia',
    "Tamaraceite": 'Canarias',
    "Urbanizacion Las Bizarricas": 'Castilla y León',
    "Aeropuerto de Noain": 'Comunidad Foral de Navarra',
    "Palau-Solita I Plegamans": 'Catalunya'
}


In [94]:
# Reemplazar los valores "Unknown" en la columna 'state' con los valores del diccionario 'lugares'
for location, state in lugares.items():
    df_final.loc[(df_final['location'] == location) & (df_final['state'] == 'Unknown'), 'state'] = state

# Mostrar las filas actualizadas para verificar
print(df_final[df_final['location'].isin(lugares.keys())][['location', 'state']])

                               location                       state
46       Castello/Castellon de La Plana        Comunitat Valenciana
81             Palau-Solita I Plegamans                   Catalunya
110      Castello/Castellon de La Plana        Comunitat Valenciana
128      Castello/Castellon de La Plana        Comunitat Valenciana
137      Castello/Castellon de La Plana        Comunitat Valenciana
161      Castello/Castellon de La Plana        Comunitat Valenciana
206      Castello/Castellon de La Plana        Comunitat Valenciana
281                           Atarrabia  Comunidad Foral de Navarra
308            Palau-Solita I Plegamans                   Catalunya
339      Castello/Castellon de La Plana        Comunitat Valenciana
390      Castello/Castellon de La Plana        Comunitat Valenciana
518    Poligono Industrial San Fernando         Comunidad de Madrid
530            Palau-Solita I Plegamans                   Catalunya
588                           Atarrabia  Comunid

Ahora por último estandarizamos el nombre de comunidad autonoma

In [100]:
df_final['state'].value_counts()

state
Andalucía                     9116
Cataluña                      7277
state de Madrid               5157
Comunidad de Madrid           3231
state Valenciana              3163
Galicia                       2640
Comunitat Valenciana          2474
Castilla-La Mancha            1889
Región de Murcia              1707
País Vasco                    1663
Extremadura                    895
Aragón                         606
Comunidad Valenciana           603
Castilla y León                424
Comunidad Foral de Navarra     379
Islas Baleares                 326
Euskadi                        286
Cantabria                      164
Asturias                       150
Navarra                        112
Asturias / Asturies             43
La Rioja                        25
Illes Balears                   19
Canarias                         5
Navarra - Nafarroa               1
Name: count, dtype: int64

In [101]:
df_final.loc[df_final['state'] == 'Catalunya', 'state'] = 'Cataluña'
df_final.loc[df_final['state'] == 'state de Madrid', 'state'] = 'Comunidad de Madrid'
df_final.loc[df_final['state'] == 'state Valenciana', 'state'] = 'Comunitat Valenciana'
df_final.loc[df_final['state'] == 'Comunidad Valenciana', 'state'] = 'Comunitat Valenciana'
df_final.loc[df_final['state'] == 'Euskadi', 'state'] = 'País Vasco'
df_final.loc[df_final['state'] == 'Islas Baleares', 'state'] = 'Illes Balears'
df_final.loc[df_final['state'] == 'Navarra - Nafarroa', 'state'] = 'Comunidad Foral de Navarra'
df_final.loc[df_final['state'] == 'Navarra', 'state'] = 'Comunidad Foral de Navarra'
df_final.loc[df_final['state'] == 'Asturias / Asturies', 'state'] = 'Principado de Asturias'
df_final.loc[df_final['state'] == 'Asturias', 'state'] = 'Principado de Asturias'




In [102]:
df_final['state'].value_counts()

state
Andalucía                     9116
Comunidad de Madrid           8388
Cataluña                      7277
Comunitat Valenciana          6240
Galicia                       2640
País Vasco                    1949
Castilla-La Mancha            1889
Región de Murcia              1707
Extremadura                    895
Aragón                         606
Comunidad Foral de Navarra     492
Castilla y León                424
Illes Balears                  345
Principado de Asturias         193
Cantabria                      164
La Rioja                        25
Canarias                         5
Name: count, dtype: int64

Exportamos el df_final a csv para empezar el análisis exploratorio de datos

In [103]:
df_final.to_csv('car_price.csv', index=False)